In [ ]:
!pip install keras==2.3.1

In [ ]:
!pip install tensorflow==1.15

In [ ]:
!pip install numpy==1.16.5

In [8]:
!pip install spacy

     |████████████████████████████████| 10.4 MB 11.8 MB/s eta 0:00:01
     |████████████████████████████████| 9.8 MB 18.8 MB/s eta 0:00:01
  Using cached catalogue-1.0.0-py2.py3-none-any.whl (7.7 kB)
  Using cached plac-1.1.3-py2.py3-none-any.whl (20 kB)
     |████████████████████████████████| 126 kB 90.4 MB/s eta 0:00:01
     |████████████████████████████████| 184 kB 111.3 MB/s eta 0:00:01
     |████████████████████████████████| 1.1 MB 21.2 MB/s eta 0:00:01
     |████████████████████████████████| 69 kB 627 kB/s s eta 0:00:01


In [9]:
!python -m spacy download en

     |████████████████████████████████| 12.0 MB 495 kB/s eta 0:00:01
  Created wheel for en-core-web-sm: filename=en_core_web_sm-2.3.1-py3-none-any.whl size=12047105 sha256=8a8cbd90fa324a1dc43658d1d64e15a22d579eab583994caf6601280ceac29c6
  Stored in directory: /tmp/pip-ephem-wheel-cache-hznslykc/wheels/10/6f/a6/ddd8204ceecdedddea923f8514e13afb0c1f0f556d2c9c3da0
Successfully built en-core-web-sm
✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')
✔ Linking successful
/home/junliw/anaconda3/envs/tensorflow1/lib/python3.6/site-packages/en_core_web_sm
-->
/home/junliw/anaconda3/envs/tensorflow1/lib/python3.6/site-packages/spacy/data/en
You can now load the model via spacy.load('en')


In [1]:
from tensorflow.python.client import device_lib 
print(device_lib.list_local_devices())
import numpy as np
import os
os.environ["CUDA_VISIBLE_DEVICES"]="0"  
import tensorflow as tf
# tf.disable_v2_behavior()
# import tensorflow-gpu as tf

from keras.preprocessing.sequence import pad_sequences
import pickle
import data_utils
import glove_utils
import models
import display_utils
from goog_lm import LM
import lm_data_utils
import lm_utils
np.random.seed(1001)
tf.set_random_seed(1001)
VOCAB_SIZE  = 50000
with open('aux_files/dataset_%d.pkl' %VOCAB_SIZE, 'rb') as f:
    dataset = pickle.load(f)
doc_len = [len(dataset.test_seqs2[i]) for i in 
           range(len(dataset.test_seqs2))]
dist_mat = np.load('aux_files/dist_counter2_%d.npy' %VOCAB_SIZE)
# Prevent returning 0 as most similar word because it is not part of the dictionary
dist_mat[0,:] = 100000
dist_mat[:,0] = 100000

skip_list = np.load('aux_files/missed_embeddings_counter_%d.npy' %VOCAB_SIZE)

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 15771051907404116074
, name: "/device:XLA_CPU:0"
device_type: "XLA_CPU"
memory_limit: 17179869184
locality {
}
incarnation: 8914181079697452717
physical_device_desc: "device: XLA_CPU device"
, name: "/device:XLA_GPU:0"
device_type: "XLA_GPU"
memory_limit: 17179869184
locality {
}
incarnation: 14722202378471669338
physical_device_desc: "device: XLA_GPU device"
, name: "/device:XLA_GPU:1"
device_type: "XLA_GPU"
memory_limit: 17179869184
locality {
}
incarnation: 11509519334892050689
physical_device_desc: "device: XLA_GPU device"
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 10988499764
locality {
  bus_id: 1
  links {
    link {
      device_id: 1
      type: "StreamExecutor"
      strength: 1
    }
  }
}
incarnation: 7870583259506579657
physical_device_desc: "device: 0, name: GeForce GTX 1080 Ti, pci bus id: 0000:01:00.0, compute capability: 6.1"
, name: "/device:GPU:1"
device_type: "G

Using TensorFlow backend.


### Demonstrating how we find the most similar words

In [ ]:
src_word = dataset.dict['elwes']
src_word

In [ ]:
for i in range(300, 305):
    src_word = i
    nearest, nearest_dist = glove_utils.pick_most_similar_words(src_word, dist_mat,20, 0.5)
        
    print('Closest to `%s` are:' %(dataset.inv_dict[src_word]))
    for w_id, w_dist in zip(nearest, nearest_dist):
          print(' -- ', dataset.inv_dict[w_id], ' ', w_dist)

    print('----')

### Preparing the dataset

In [2]:
max_len = 250
train_x = pad_sequences(dataset.train_seqs2, maxlen=max_len, padding='post')
train_y = np.array(dataset.train_y)
test_x = pad_sequences(dataset.test_seqs2, maxlen=max_len, padding='post')
test_y = np.array(dataset.test_y)

### Loading the sentiment analysis model

In [3]:
tf.reset_default_graph()
if tf.get_default_session():
    sess.close()
sess = tf.Session()
batch_size = 1
lstm_size = 128
#max_len =  100

with tf.variable_scope('imdb', reuse=False):
    model = models.SentimentModel(batch_size=batch_size,
                           lstm_size = lstm_size,
                           max_len = max_len,
                           embeddings_dim=300, vocab_size=dist_mat.shape[1],is_train = False)
saver = tf.train.Saver()
saver.restore(sess, './models/imdb_model')



The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.

Instructions for updating:
This class is equivalent as tf.keras.layers.LSTMCell, and will be replaced by that in Tensorflow 2.0.
Instructions for updating:
Please use `keras.layers.RNN(cell)`, which is equivalent to this API
Instructions for updating:
Please use `layer.add_weight` method instead.
Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backpr

## Loading the Google Language model

In [4]:
goog_lm = LM()


LM vocab loading done
Instructions for updating:
Use tf.gfile.GFile.



Recovering graph.



INFO:tensorflow:Recovering Graph goog_lm/graph-2016-09-10.pbtxt


Recovering checkpoint goog_lm/ckpt-*


In [5]:
import spacy
nlp = spacy.load("en",disable=['parser', 'ner'])
def print_fine_pos(token):
    return (token.tag_)
def pos_tags(sentence):
    #sentence = unicode(sentence, "utf-8")
    tokens = nlp(sentence)
    tags = []
    for tok in tokens:
        tags.append((tok,print_fine_pos(tok)))
    return tags
a = "UNK"
print(pos_tags(a))

[(UNK, 'NNP')]


In [14]:
b = np.array(["1","2","3"])
c=b!="3"

In [15]:
len(c)

3

In [17]:
np.pad(c,(0,1),constant_values=1)

array([ True,  True, False,  True])

In [18]:
c.shape

(3,)

#### demonstrating the GoogLM

In [ ]:
src_word = dataset.dict['play']
nearest, nearest_dist = glove_utils.pick_most_similar_words(src_word, dist_mat,20)
nearest_w = [dataset.inv_dict[x] for x in nearest]
print('Closest to `%s` are %s' %(dataset.inv_dict[src_word], nearest_w))

In [ ]:
prefix = 'is'
suffix = 'with'
lm_preds = goog_lm.get_words_probs(prefix, nearest_w, suffix)
print('most probable is ', nearest_w[np.argmax(lm_preds)])


## Try Attack

In [6]:
from attacks import GeneticAtack, PerturbSentBaseline,PerturbSentBaseline_Greedy,GeneticAtackImproved,ParticleSwampAttack

## Main Attack 

In [7]:
pop_size = 32
n1 = 8

with tf.variable_scope('imdb', reuse=True):
    batch_model = models.SentimentModel(batch_size=pop_size,
                           lstm_size = lstm_size,
                           max_len = max_len,
                           embeddings_dim=300, vocab_size=dist_mat.shape[1],is_train = False)
    
with tf.variable_scope('imdb', reuse=True):
    neighbour_model = models.SentimentModel(batch_size=n1,
                           lstm_size = lstm_size,
                           max_len = max_len,
                           embeddings_dim=300, vocab_size=dist_mat.shape[1],is_train = False)
import time
TEST_SIZE = 1000
test_idx = np.random.choice(len(dataset.test_y), TEST_SIZE, replace=False)
print(test_idx[:3])

[22589 13005  7772]


In [11]:
ga_atttack = GeneticAtack(sess, model, batch_model, neighbour_model, dataset, dist_mat, 
                                  skip_list,
                                  goog_lm, max_iters=30, 
                                   pop_size=pop_size,
                                  
                                  n1 = n1,
                                  n2 = 4,
                                 use_lm =      True, use_suffix=False)

In [10]:
gai_atttack = GeneticAtackImproved(sess, model, batch_model, neighbour_model, dataset, dist_mat, 
                                  skip_list,
                                  pos_tags, max_iters=30, 
                                   pop_size=pop_size,
                                  n1 = n1,
                                  n2 = 4,delta=0.8,
                                 use_lm =      True, use_suffix=False)

In [19]:
test_len = []
for i in range(TEST_SIZE):
    test_len.append(len(dataset.test_seqs2[test_idx[i]]))
print('Shortest sentence in our test set is %d words' %np.min(test_len))

test_list = []
orig_list = []
orig_label_list = []
adv_list = []
dist_list = []

times = []
for i in range(TEST_SIZE):
# for x in [ 9554, 20939,  5709,  5105,  7783,  1064,  8223, 19317, 19096]:
#     k = x
    k = test_idx[i]
    x_orig = test_x[k]
    orig_label = test_y[k]
    orig_preds=  model.predict(sess, x_orig[np.newaxis, :])[0]
    # print(orig_label, orig_preds, np.argmax(orig_preds))
    if np.argmax(orig_preds) != orig_label:
#         print('skipping wrong classifed ..')
#         print('--------------------------')
        continue
    x_len = np.sum(np.sign(x_orig))
    if x_len >= 100:
#         print('skipping too long input..')
#         print('--------------------------')
        continue
    # if np.max(orig_preds) < 0.90:
    #    print('skipping low confidence .. \n-----\n')
    #    continue
    print(k)
    print('****** ', len(test_list) + 1, ' ********')
    test_list.append(k)
    orig_list.append(x_orig)
    target_label = 1 if orig_label == 0 else 0
    orig_label_list.append(orig_label)
    start = time.time()
#     x_adv = gai_atttack.attack( x_orig, target_label)
    x_adv = ga_atttack.attack( x_orig, target_label)
    end = time.time()
    
    times.append(end-start)
    adv_list.append(x_adv)
    if x_adv is None:
        print('%d failed' %(k))
        dist_list.append(100000)
    else:
        num_changes = np.sum(x_orig != x_adv)
        print('%d - %d changed.' %(k, num_changes))
        dist_list.append(num_changes)
        # display_utils.visualize_attack(sess, model, dataset, x_orig, x_adv)
    print('--------------------------')
    if (len(test_list)>= 50):
        break

Shortest sentence in our test set is 18 words
5402
******  1  ********
		 0  --  0.102694795
start
finish
		 1  --  0.14421032
start
finish
		 2  --  0.24677394
start
finish
		 3  --  0.35291624
start
finish
		 4  --  0.42670944
start
finish
		 5  --  0.80595416
5402 - 8 changed.
--------------------------
9554
******  2  ********
		 0  --  0.31298915
start
finish
		 1  --  0.5575139
9554 - 3 changed.
--------------------------
9569
******  3  ********
		 0  --  0.17642051
start
finish
		 1  --  0.2333814
start
finish
		 2  --  0.5371336
9569 - 2 changed.
--------------------------
2504
******  4  ********
		 0  --  0.56479114
2504 - 1 changed.
--------------------------
3979
******  5  ********
		 0  --  0.6883316
3979 - 1 changed.
--------------------------
20939
******  6  ********
		 0  --  0.01775397
start
finish
		 1  --  0.01944709
start
finish
		 2  --  0.03180861
start
finish
		 3  --  0.034361128
start
finish
		 4  --  0.043855842
start
finish
		 5  --  0.0440667
start
finish

		 0  --  0.00033909307
start
finish
		 1  --  0.0039524585
start
finish
		 2  --  0.009800364
start
finish
		 3  --  0.16966902
start
finish
		 4  --  0.58244586
13695 - 7 changed.
--------------------------
11787
******  31  ********
		 0  --  0.2567895
start
finish
		 1  --  0.49644142
start
finish
		 2  --  0.50924474
11787 - 2 changed.
--------------------------
17183
******  32  ********
		 0  --  0.7650145
17183 - 1 changed.
--------------------------
4805
******  33  ********
		 0  --  0.48884395
start
finish
		 1  --  0.5551822
4805 - 2 changed.
--------------------------
9303
******  34  ********
		 0  --  0.08434058
start
finish
		 1  --  0.08434058
start
finish
		 2  --  0.115089215
start
finish
		 3  --  0.27544507
start
finish
		 4  --  0.39979285
start
finish
		 5  --  0.9439759
9303 - 11 changed.
--------------------------
24320
******  35  ********
		 0  --  0.08199687
start
finish
		 1  --  0.11381114
start
finish
		 2  --  0.19667658
start
finish
		 3  --  0.2983342


In [20]:
with open('ga_results1.pkl', 'wb') as f:
    pickle.dump((orig_list, orig_label_list, adv_list, dist_list,times), f)

# 1 Attack Baseline

In [21]:
base_atttack = PerturbSentBaseline(sess, model, neighbour_model, dataset, dist_mat, 
                                  goog_lm,                                 
                                  n1 = n1,
                                  n2 = 4,
                                 use_lm =      False)

In [22]:

test_len = []
for i in range(TEST_SIZE):
    test_len.append(len(dataset.test_seqs2[test_idx[i]]))
print('Shortest sentence in our test set is %d words' %np.min(test_len))

test_list2 = []
orig_list2 = []
orig_label_list2 = []
adv_list2 = []
dist_list2 = []
times2 = []

for i in range(56,TEST_SIZE):
    x_orig = test_x[test_idx[i]]
    orig_label = test_y[test_idx[i]]
    orig_preds=  model.predict(sess, x_orig[np.newaxis, :])[0]
    print(orig_preds)
    # print(orig_label, orig_preds, np.argmax(orig_preds))
    if np.argmax(orig_preds) != orig_label:
#         print('skipping wrong classifed ..')
#         print('--------------------------')
        continue
    x_len = np.sum(np.sign(x_orig))
    if x_len >= 100:
#         print('skipping too long input..')
#         print('--------------------------')
        continue
    # if np.max(orig_preds) < 0.90:
    #    print('skipping low confidence .. \n-----\n')
    #    continue
    print(i)
    print('****** ', len(test_list2) + 1, ' ********')
    test_list2.append(test_idx[i])
    orig_list2.append(x_orig)
    target_label = 1 if orig_label == 0 else 0
    orig_label_list2.append(orig_label)
    start = time.time()
    print("orig",x_orig)
    x_adv = base_atttack.attack( x_orig, target_label)
    print("after after",x_adv)
    end = time.time()
    times2.append(end-start)
    adv_list2.append(x_adv)
    if x_adv is None:
        print('%d failed' %(i+1))
        dist_list2.append(100000)
    else:
        num_changes = np.sum(x_orig != x_adv)
        print('%d - %d changed.' %(i+1, num_changes))
        dist_list2.append(num_changes)
        # display_utils.visualize_attack(sess, model, dataset, x_orig, x_adv)
    print('--------------------------')
    if (len(test_list2)>= 50):
        break

Shortest sentence in our test set is 18 words
[0.98665303 0.013347  ]
[9.9995255e-01 4.7417878e-05]
57
******  1  ********
orig [   47     6  1194     8   130     1 14651     4     3   539    45  2487
  6511    62     9     6 13974    31   447  6210    83     1   281     6
    40   370    57     1  3280   153    23   370     1   806     6  1639
     2  4562     1   111 10551   364  6761    11   183   326    37     3
  1765    17    71   153   167   140     3  1133   140   573  1330     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0   

length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8


[5.5296172e-05 9.9994469e-01]
[0.5344732  0.46552685]
[0.00693287 0.99306715]
[0.9977869  0.00221305]
[0.8080659  0.19193406]
[9.5436655e-05 9.9990451e-01]
[9.9999869e-01 1.2622986e-06]
[0.7838679  0.21613203]
[0.99876547 0.00123456]
[3.2803364e-08 1.0000000e+00]
[0.00167146 0.9983285 ]
124
******  6  ********
orig [  16   29    4    1 1476   99   43  635   42  251    5  166  139   22
   67  190    1  223  220    5   64   58  359  444    9    9   13   49
 2170  250   10   59  542  383    9    5  256   34  490    5  190    1
  223  220   43   15    3  324 2189   30    1   99    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    

length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 0
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8


length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8


...

length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
after after None
479 failed
--------------------------
[0.9709573  0.02904264]
[0.9892129  0.01078719]
480
******  42  ********
orig [   58   366     2    10  1605    11    17 22893     9    15   157    28
    41 28767 50000  1228 17567    14    32   202   629     6   639     1
    17     6    35   

length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
after after None
482 failed
--------------------------
[9.9983156e-01 1.6841845e-04]
[3.8475156e-04 9.9961519e-01]
483
******  44  ********
orig [   15     3  1416   558     1   633   133    16 17982 11478     2     1
     7     7 10777  1445     6  1045   471   239   791    38     5    58
  2092   338    96   115  1364    17     4    29    55    18    16     3
  1005     1   545   136    23  1187  7878  7552  3841    32 21519    22
  5390    76     5    64   172   248     2  1660 13882     6  1156     2
    52   864    14    32  3553   159 10430   724   306    53     1 20763
    31    98   814  1664    84   507   785   155  6255  4604  1528     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0     0     0     0     0     0     0     0     0
     0     0     0     0 

length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8


length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 0
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8


length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
length of replace list 8
after after [  11    6  239    1   61   17   10   25  123   21   74  499    5   94
    9   29    1   93  140   21   61   13    9  613    2  354   18    1
 6124  362 1231   90    9  251    5   94   43    1  202    2    8   46
 2936    1  411  795   11   28   37    1 3191    0    0    0    0    0
    0    0    0    0    0    

In [23]:
with open('base_results1.pkl', 'wb') as f:
    pickle.dump((orig_list2, orig_label_list2, adv_list2, dist_list2,times2), f)

# Greedy Baseline

In [24]:
base_atttack = PerturbSentBaseline_Greedy(sess, model, neighbour_model, dataset, dist_mat, 
                                  goog_lm,                                 
                                  n1 = n1,
                                  n2 = 4,
                                 use_lm =      True)

In [25]:

test_len = []
for i in range(TEST_SIZE):
    test_len.append(len(dataset.test_seqs2[test_idx[i]]))
print('Shortest sentence in our test set is %d words' %np.min(test_len))

test_list3 = []
orig_list3 = []
orig_label_list3 = []
adv_list3 = []
dist_list3 = []
times3 = []

for i in range(TEST_SIZE):
    x_orig = test_x[test_idx[i]]
    orig_label = test_y[test_idx[i]]
    orig_preds=  model.predict(sess, x_orig[np.newaxis, :])[0]
    # print(orig_label, orig_preds, np.argmax(orig_preds))
    if np.argmax(orig_preds) != orig_label:
#         print('skipping wrong classifed ..')
#         print('--------------------------')
        continue
    x_len = np.sum(np.sign(x_orig))
    if x_len >= 100:
#         print('skipping too long input..')
#         print('--------------------------')
        continue
    # if np.max(orig_preds) < 0.90:
    #    print('skipping low confidence .. \n-----\n')
    #    continue
    print(i)
    print('****** ', len(test_list3) + 1, ' ********')
    test_list3.append(test_idx[i])
    orig_list3.append(x_orig)
    target_label = 1 if orig_label == 0 else 0
    orig_label_list3.append(orig_label)
    start = time.time()
    x_adv = base_atttack.attack( x_orig, target_label)
    end = time.time()
    times3.append(end-start)
    adv_list3.append(x_adv)
    if x_adv is None:
        print('%d failed' %(i+1))
        dist_list3.append(100000)
    else:
        num_changes = np.sum(x_orig != x_adv)
        print('%d - %d changed.' %(i+1, num_changes))
        dist_list3.append(num_changes)
        # display_utils.visualize_attack(sess, model, dataset, x_orig, x_adv)
    print('--------------------------')
    if (len(test_list3)>= 50):
        break

Shortest sentence in our test set is 18 words
8
******  1  ********
Document length = 97
 --- 0 / 97 
9 - 14 changed.
--------------------------
14
******  2  ********
Document length = 18
 --- 0 / 18 
15 - 10 changed.
--------------------------
19
******  3  ********
Document length = 87
 --- 0 / 87 
20 - 21 changed.
--------------------------
27
******  4  ********
Document length = 59
 --- 0 / 59 
28 - 2 changed.
--------------------------
31
******  5  ********
Document length = 63
 --- 0 / 63 
32 - 1 changed.
--------------------------
34
******  6  ********
Document length = 56
 --- 0 / 56 
35 - 28 changed.
--------------------------
41
******  7  ********
Document length = 40
 --- 0 / 40 
42 - 16 changed.
--------------------------
43
******  8  ********
Document length = 82
 --- 0 / 82 
44 - 20 changed.
--------------------------
51
******  9  ********
Document length = 53
 --- 0 / 53 
52 - 22 changed.
--------------------------
53
******  10  ********
Document length = 59
 ---

In [26]:
with open('greedy_results1.pkl', 'wb') as f:
    pickle.dump((orig_list3, orig_label_list3, adv_list3, dist_list3,times3), f)

# Improved Genetic Attack

In [17]:
gai_atttack = GeneticAtackImproved(sess, model, batch_model, neighbour_model, dataset, dist_mat, 
                                  skip_list,
                                  pos_tags, max_iters=30, 
                                   pop_size=pop_size,
                                  n1 = n1,
                                  n2 = 4,
                                 use_lm =      True, use_suffix=False)

In [18]:

test_len = []
for i in range(TEST_SIZE):
    test_len.append(len(dataset.test_seqs2[test_idx[i]]))
print('Shortest sentence in our test set is %d words' %np.min(test_len))

test_list4 = []
orig_list4 = []
orig_label_list4 = []
adv_list4 = []
dist_list4 = []
times4 = []

for i in range(TEST_SIZE):
    x_orig = test_x[test_idx[i]]
    orig_label = test_y[test_idx[i]]
    orig_preds=  model.predict(sess, x_orig[np.newaxis, :])[0]
    if np.argmax(orig_preds) != orig_label:
        continue
    x_len = np.sum(np.sign(x_orig))
    if x_len >= 100:
        continue
    print(i)
    print('****** ', len(test_list4) + 1, ' ********')
    test_list4.append(test_idx[i])
    orig_list4.append(x_orig)
    target_label = 1 if orig_label == 0 else 0
    orig_label_list4.append(orig_label)
    start = time.time()
    x_adv = gai_atttack.attack( x_orig, target_label)
    end = time.time()
    times4.append(end-start)
    adv_list4.append(x_adv)
    if x_adv is None:
        print('%d failed' %(i+1))
        dist_list4.append(100000)
    else:
        num_changes = np.sum(x_orig != x_adv)
        print('%d - %d changed.' %(i+1, num_changes))
        dist_list4.append(num_changes)
        # display_utils.visualize_attack(sess, model, dataset, x_orig, x_adv)
    print('--------------------------')
    if (len(test_list4)>= 50):
        break

Shortest sentence in our test set is 18 words
8
******  1  ********
		 0  --  0.015231195
start
finish
		 1  --  0.03566935
start
finish
		 2  --  0.2710237
start
finish
		 3  --  0.2710237
start
finish
		 4  --  0.4212082
start
finish
		 5  --  0.64994675
9 - 4 changed.
--------------------------
14
******  2  ********
		 0  --  0.27091888
start
finish
		 1  --  0.3125503
start
finish
		 2  --  0.34606737
start
finish
		 3  --  0.3489812
start
finish
		 4  --  0.3497946
start
finish
		 5  --  0.3497946
start
finish
		 6  --  0.3497946
start
finish
		 7  --  0.3497946
start
finish
		 8  --  0.3497946
start
finish
		 9  --  0.3497946
start
finish
		 10  --  0.3497946
start
finish
		 11  --  0.3497946
start
finish
		 12  --  0.3497946
start
finish
		 13  --  0.3497946
start
finish
		 14  --  0.3497946
start
finish
		 15  --  0.3497946
start
finish
		 16  --  0.3497946
start
finish
		 17  --  0.3497946
start
finish
		 18  --  0.3497946
start
finish
		 19  --  0.3497946
start
finish
		 20 

finish
		 5  --  0.0059964233
start
finish
		 6  --  0.0066568595
start
finish
		 7  --  0.015142947
start
finish
		 8  --  0.015142947
start
finish
		 9  --  0.018521063
start
finish
		 10  --  0.018521063
start
finish
		 11  --  0.023532068
start
finish
		 12  --  0.023532068
start
finish
		 13  --  0.029307006
start
finish
		 14  --  0.029307006
start
finish
		 15  --  0.02969464
start
finish
		 16  --  0.03644069
start
finish
		 17  --  0.03644069
start
finish
		 18  --  0.03644069
start
finish
		 19  --  0.03644069
start
finish
		 20  --  0.03644069
start
finish
		 21  --  0.040601037
start
finish
		 22  --  0.040601037
start
finish
		 23  --  0.040601037
start
finish
		 24  --  0.043159854
start
finish
		 25  --  0.043679368
start
finish
		 26  --  0.043679368
start
finish
		 27  --  0.043679368
start
finish
		 28  --  0.043679368
start
finish
		 29  --  0.043679368
start
finish
252 failed
--------------------------
255
******  23  ********
		 0  --  0.18794043
start
finish
		 1 

finish
		 26  --  0.11538291
start
finish
		 27  --  0.11538291
start
finish
		 28  --  0.11538291
start
finish
		 29  --  0.120205306
start
finish
360 failed
--------------------------
367
******  38  ********
		 0  --  0.0065006074
start
finish
		 1  --  0.00864945
start
finish
		 2  --  0.022295061
start
finish
		 3  --  0.032688133
start
finish
		 4  --  0.04807345
start
finish
		 5  --  0.087178186
start
finish
		 6  --  0.087178186
start
finish
		 7  --  0.123974636
start
finish
		 8  --  0.123974636
start
finish
		 9  --  0.15947278
start
finish
		 10  --  0.15947278
start
finish
		 11  --  0.22531074
start
finish
		 12  --  0.22531074
start
finish
		 13  --  0.22531074
start
finish
		 14  --  0.29312137
start
finish
		 15  --  0.29802462
start
finish
		 16  --  0.29802462
start
finish
		 17  --  0.3371752
start
finish
		 18  --  0.47075248
start
finish
		 19  --  0.52982545
368 - 16 changed.
--------------------------
396
******  39  ********
		 0  --  0.0049260533
start
finish

In [19]:
with open('gai_results1.pkl', 'wb') as f:
    pickle.dump((orig_list4, orig_label_list4, adv_list4, dist_list4,times4), f)

In [28]:
temp = np.array(dist_list4)==100000
wrongs =np.array(test_list4)[temp]
wrongs

array([ 9554, 20939,  5709,  5105,  7783,  1064,  8223, 19317, 19096])

# PS Attack

In [27]:
ps_atttack = ParticleSwampAttack(sess, model, batch_model, neighbour_model, dataset, dist_mat, 
                                  skip_list,
                                  goog_lm, max_iters=30, 
                                   pop_size=pop_size,
                                  n1 = n1,
                                  n2 = 4,
                                 use_lm =      True, use_suffix=False)

In [28]:
test_len = []
for i in range(TEST_SIZE):
    test_len.append(len(dataset.test_seqs2[test_idx[i]]))
print('Shortest sentence in our test set is %d words' %np.min(test_len))

test_list5 = []
orig_list5 = []
orig_label_list5 = []
adv_list5 = []
dist_list5 = []
times5 = []

for i in range(TEST_SIZE):
    x_orig = test_x[test_idx[i]]
    orig_label = test_y[test_idx[i]]
    orig_preds=  model.predict(sess, x_orig[np.newaxis, :])[0]
    if np.argmax(orig_preds) != orig_label:
        continue
    x_len = np.sum(np.sign(x_orig))
    if x_len >= 100:
        continue
    print(i)
    print('****** ', len(test_list5) + 1, ' ********')
    test_list5.append(test_idx[i])
    orig_list5.append(x_orig)
    target_label = 1 if orig_label == 0 else 0
    orig_label_list5.append(orig_label)
    start = time.time()
    x_adv = ps_atttack.attack( x_orig, target_label)
    end = time.time()
    times5.append(end-start)
    adv_list5.append(x_adv)
    if x_adv is None:
        print('%d failed' %(i+1))
        dist_list5.append(100000)
    else:
        num_changes = np.sum(x_orig != x_adv)
        print('%d - %d changed.' %(i+1, num_changes))
        dist_list5.append(num_changes)
        # display_utils.visualize_attack(sess, model, dataset, x_orig, x_adv)
    print('--------------------------')
    if (len(test_list5)>= 50):
        break

Shortest sentence in our test set is 18 words
8
******  1  ********
**  though
[3024  258 8912  463 2185 2942 1861  187]
['albeit', 'although', 'notwithstanding', 'despite', 'nevertheless', 'nonetheless', 'whilst', 'however', 'though']
[-1.0000000e+07 -1.4165109e-03 -1.0000000e+07  7.7570556e-04
 -1.0000000e+07 -1.0000000e+07 -5.5597816e-04  1.2130267e-03]
7
**  story
[  784  2943   534  2802 26538   476 21574 11722]
['tale', 'tales', 'stories', 'storytelling', 'histories', 'history', 'conte', 'narratives', 'story']
[-1.0000000e+07 -1.1065882e-03 -8.4116124e-05 -1.0000000e+07
 -1.0000000e+07 -3.3552106e-04 -1.0000000e+07 -6.2028877e-04]
2
**  peter
[37005.  5051.  5823. 11272. 25014.     0.     0.     0.]
['petr', 'peters', 'pete', 'pedro', 'petra', 'UNK', 'UNK', 'UNK', 'peter']
[-1.0000000e+07 -9.0796966e-05 -4.9032038e-04 -6.0389191e-04
  9.6214982e-04 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07]
4
**  all
[  172   282   433 28028   313   223  1459  6322]
['every', 'everything', 'en

[-3.4511229e-04  1.3581347e-03 -1.5730131e-04  2.5457214e-03
 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07]
3
**  very
[  542 12912   573  6136   176 12691    73  8113]
['highly', 'eminently', 'extremely', 'hugely', 'quite', 'supremely', 'much', 'enormously', 'very']
[-1.0085758e-03 -1.0000000e+07  6.6596270e-04 -1.0000000e+07
 -7.6078251e-04 -1.0000000e+07  4.7699083e-05 -1.0000000e+07]
2
**  beat
[ 3941 47186 13166 22571 34752 29531  3315 32994]
['beats', 'trounced', 'defeats', 'overpowered', 'overpowers', 'overpower', 'beating', 'rout', 'beat']
[-6.9963513e-04 -1.0000000e+07  6.7052711e-04 -1.0000000e+07
 -1.0000000e+07 -1.0000000e+07  1.9740174e-04  2.4526487e-03]
7
[0.0073038  0.00609078 0.00705293 0.00673295 0.01371743 0.00636025
 0.00673295 0.00827679 0.00655653 0.00685042 0.00705293 0.00627213
 0.00673295 0.00696222 0.00675674 0.00696747 0.00701813 0.00673295
 0.00873387 0.00609078 0.02131176 0.00609078 0.02652662 0.00609078
 0.00696747 0.0191687  0.00609078 0.00

[ 1.8061092e-04 -2.8082635e-05 -1.0000000e+07 -1.0000000e+07
 -1.0000000e+07 -1.0000000e+07  8.7668933e-04  3.2308628e-03]
7
**  obviously
[ 5546   692 41802  1952 14070   681 12910   404]
['evidently', 'clearly', 'manifestly', 'naturally', 'patently', 'apparently', 'plainly', 'definitely', 'obviously']
[ 1.8135039e-04 -2.4187695e-03 -1.0000000e+07 -1.0000000e+07
 -1.0000000e+07 -2.4021789e-04 -1.0000000e+07 -4.6303710e-03]
0
**  good
[ 2661. 38463.    70.   324.   539.   115.     0.     0.]
['alright', 'buena', 'well', 'nice', 'decent', 'best', 'UNK', 'UNK', 'good']
[-1.0000000e+07 -1.0000000e+07 -3.5704160e-04  1.3677077e-04
  7.5964723e-04 -2.1723411e-03 -1.0000000e+07 -1.0000000e+07]
4
**  era
[45656. 43490. 12645.     0.     0.     0.     0.     0.]
['epoch', 'epochs', 'eras', 'UNK', 'UNK', 'UNK', 'UNK', 'UNK', 'era']
[ 1.30625535e-02 -7.11918995e-03 -2.45241262e-03  1.86264515e-08
 -1.00000000e+07 -1.00000000e+07 -1.00000000e+07 -1.00000000e+07]
0
**  little
[  389 19028 14712 28

[-2.3604203e-03 -1.0000000e+07 -2.2186525e-03 -1.0000000e+07
 -1.0000000e+07 -1.0000000e+07 -4.9226545e-04  3.6535487e-03]
7
**  into
[  30  464  946 1841    8 5356   15 1641]
['at', 'under', 'towards', 'toward', 'in', 'en', 'for', 'onto', 'into']
[ 2.8733909e-04  4.0408876e-04 -1.0000000e+07 -1.0000000e+07
 -2.5868742e-04 -1.0000000e+07  4.5113312e-04 -1.0000000e+07]
6
**  anyone
[1846  291 1814 1459  313 2501  412 1334]
['somebody', 'someone', 'anybody', 'everybody', 'everyone', 'whoever', 'person', 'nobody', 'anyone']
[-1.0000000e+07  6.7671994e-04 -1.0000000e+07 -7.5885560e-04
  5.2733347e-05 -1.0000000e+07  3.1947624e-04 -1.0000000e+07]
1
**  all
[  172   282   433 28028   313   223  1459  6322]
['every', 'everything', 'entire', 'totality', 'everyone', 'whole', 'everybody', 'entirety', 'all']
[-1.2344494e-04 -4.1512549e-03 -1.0000000e+07 -1.0000000e+07
 -5.9497170e-04  5.2867252e-03 -1.0000000e+07 -1.0000000e+07]
5
**  beat
[ 3941 47186 13166 22571 34752 29531  3315 32994]
['beats

[-8.6776167e-03 -1.4636174e-02 -1.0626242e-02 -1.2635872e-02
 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07]
0
**  act
[1418. 1161. 5770. 4473.    0.    0.    0.    0.]
['acts', 'law', 'lois', 'laws', 'UNK', 'UNK', 'UNK', 'UNK', 'act']
[-3.9850846e-03  1.3392493e-03 -9.0004206e-03 -7.2041154e-04
 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07]
1
**  beat
[ 3941 47186 13166 22571 34752 29531  3315 32994]
['beats', 'trounced', 'defeats', 'overpowered', 'overpowers', 'overpower', 'beating', 'rout', 'beat']
[-5.8901943e-03 -1.0000000e+07 -2.2975579e-03 -1.0000000e+07
 -1.0000000e+07 -1.0000000e+07  1.3799220e-04  1.2264200e-02]
7
**  very
[  542 12912   573  6136   176 12691    73  8113]
['highly', 'eminently', 'extremely', 'hugely', 'quite', 'supremely', 'much', 'enormously', 'very']
[-1.6791120e-02 -1.0000000e+07  4.8382804e-03 -1.0000000e+07
 -1.0161959e-02 -1.0000000e+07  2.8495491e-04 -1.0000000e+07]
2
**  very
[  542 12912   573  6136   176 12691    73  811

...

[-1.0000000e+07  4.5329928e-03  1.8235579e-02  2.1289885e-02
 -1.1463739e-02 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07]
3
**  lovely
[ 1906  2248  8802  7486   304  1217  1485 18019]
['delightful', 'handsome', 'ravishing', 'enchanting', 'beautiful', 'charming', 'gorgeous', 'charmer', 'lovely']
[-1.00000000e+07  3.63777503e-02 -1.00000000e+07 -1.00000000e+07
 -1.13634765e-02 -6.77836686e-03  4.00033593e-03 -1.00000000e+07]
1
**  brilliant
[45413  3612  9815  1992   774  9696   386  2994]
['resplendent', 'splendid', 'wondrous', 'magnificent', 'fantastic', 'marvellous', 'wonderful', 'marvelous', 'brilliant']
[-1.0000000e+07  5.9758872e-04 -1.0000000e+07 -1.0000000e+07
  4.7691166e-04 -1.0000000e+07  1.1094846e-03 -5.5095553e-04]
6
**  lovely
[ 1906  2248  8802  7486   304  1217  1485 18019]
['delightful', 'handsome', 'ravishing', 'enchanting', 'beautiful', 'charming', 'gorgeous', 'charmer', 'lovely']
[-1.00000000e+07  3.63777503e-02 -1.00000000e+07 -1.00000000e+07
 -1.13634765e-02 -6.7

[ 4.202161e-03  1.348257e-04  3.736239e-02  0.000000e+00 -1.000000e+07
 -1.000000e+07 -1.000000e+07 -1.000000e+07]
2
**  anyone
[1846  291 1814 1459  313 2501  412 1334]
['somebody', 'someone', 'anybody', 'everybody', 'everyone', 'whoever', 'person', 'nobody', 'anyone']
[-1.0000000e+07 -1.0000000e+07 -1.0000000e+07 -3.2397322e-03
 -4.1677225e-03 -1.0000000e+07 -3.0984357e-04  1.1932503e-02]
7
finish
[0.07484999 0.04521506 0.13251759 0.11122773 0.04632452 0.11122773
 0.12646218 0.05698866 0.03750832 0.0313034  0.17067571 0.12045469
 0.03149296 0.03660161 0.11122773 0.03204608 0.08790037 0.05698866
 0.0618638  0.07615739 0.05055298 0.09024446 0.07615739 0.112783
 0.03444168 0.09198143 0.05532498 0.07749285 0.07615739 0.07564714
 0.06866579 0.0432359 ]
		 1  --  0.17067571
start
**  brilliant
[45413  3612  9815  1992   774  9696   386  2994]
['resplendent', 'splendid', 'wondrous', 'magnificent', 'fantastic', 'marvellous', 'wonderful', 'marvelous', 'brilliant']
[-1.0000000e+07 -1.0000000e+

[-1.0000000e+07 -1.5436560e-03 -1.0000000e+07 -1.0000000e+07
  2.6977360e-03 -1.0000000e+07  2.3315400e-03 -3.1288415e-03]
4
**  brilliant
[45413  3612  9815  1992   774  9696   386  2994]
['resplendent', 'splendid', 'wondrous', 'magnificent', 'fantastic', 'marvellous', 'wonderful', 'marvelous', 'brilliant']
[-1.0000000e+07 -1.5436560e-03 -1.0000000e+07 -1.0000000e+07
  2.6977360e-03 -1.0000000e+07  2.3315400e-03 -3.1288415e-03]
4
**  wonderful
[1303 9696 2994 1992  774 3612 9815 1485]
['terrific', 'marvellous', 'marvelous', 'magnificent', 'fantastic', 'splendid', 'wondrous', 'gorgeous', 'wonderful']
[-1.0000000e+07 -1.0000000e+07 -1.6890001e-03 -1.6437061e-03
 -3.5478882e-03 -1.0000000e+07 -1.0000000e+07  2.5685258e-02]
7
**  wonderful
[1303 9696 2994 1992  774 3612 9815 1485]
['terrific', 'marvellous', 'marvelous', 'magnificent', 'fantastic', 'splendid', 'wondrous', 'gorgeous', 'wonderful']
[-1.0000000e+07 -1.0000000e+07 -1.0432541e-02 -7.6377094e-03
 -2.2483692e-02 -1.0000000e+07 -1

[-1.0000000e+07  1.6106948e-02 -1.0000000e+07 -1.0000000e+07
 -4.4379570e-03 -3.1405427e-03  1.9835681e-03 -1.0000000e+07]
1
**  wonderful
[1303 9696 2994 1992  774 3612 9815 1485]
['terrific', 'marvellous', 'marvelous', 'magnificent', 'fantastic', 'splendid', 'wondrous', 'gorgeous', 'wonderful']
[-1.0000000e+07 -1.0000000e+07 -1.6890001e-03 -1.6437061e-03
 -1.0000000e+07  3.1822920e-04 -1.0000000e+07  2.5685258e-02]
7
**  see
[ 5587. 49913.   316.   165.  3614.     0.     0.     0.]
['behold', 'consults', 'seeing', 'look', 'admire', 'UNK', 'UNK', 'UNK', 'see']
[ 1.7990582e-03 -1.0000000e+07  1.0241777e-02  1.1683233e-02
 -6.2236637e-03 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07]
3
**  captain
[18531. 17642.  9515.  5648. 46218. 34903.     0.     0.]
['skipper', 'captains', 'capt', 'commander', 'commandant', 'commanders', 'UNK', 'UNK', 'captain']
[-5.2713763e-02 -4.2595759e-02 -1.0000000e+07 -3.8186356e-02
 -1.0000000e+07 -3.6656998e-02 -1.0000000e+07 -1.0000000e+07]
5
**  including


[ 2.0812731e-03  4.9168859e-03  6.1120652e-04 -1.0000000e+07
 -1.0000000e+07  2.1176971e-03 -1.0000000e+07 -1.0000000e+07]
1
**  great
[ 1756  3516  1187  6845  1303 26792  1992   386]
['grand', 'tremendous', 'awesome', 'phenomenal', 'terrific', 'prodigious', 'magnificent', 'wonderful', 'great']
[-4.1896151e-03 -1.0000000e+07 -1.7274056e-02 -1.0000000e+07
 -1.0000000e+07 -1.0000000e+07  1.2705196e-01  5.9083138e-02]
6
**  bad
[18317  5461  4477 37017  3804  1565 35255  3814]
['mala', 'naughty', 'rotten', 'amiss', 'wicked', 'negative', 'unfavourable', 'horrid', 'bad']
[-1.0000000e+07  2.5419724e-01 -1.2606322e-02 -1.0000000e+07
  5.0645667e-01  1.2694629e-01 -1.0000000e+07 -1.0000000e+07]
4
**  accent
[ 1148  4252  4100 12663  6463  9282  9180  2457]
['focus', 'emphasis', 'focusing', 'concentrating', 'concentrate', 'concentrates', 'concentrated', 'focused', 'accent']
[ 2.8296616e-03  3.8393419e-03 -1.0000000e+07  7.3085763e-03
 -1.0000000e+07 -1.0000000e+07 -1.0000000e+07  1.2661926e-03

In [29]:
with open('ps_results.pkl', 'wb') as f:
    pickle.dump((orig_list5, orig_label_list5, adv_list5, dist_list5,times5), f)

## Visualize some output results

In [30]:
orig_list, orig_label_list, adv_list, dist_list,times = pickle.load(open("ga_results1.pkl","rb"))
success_rate = [0 if dist_list[i] ==100000 else 1 for i in range(len(dist_list))]
orig_len = [np.sum(np.sign(x)) for x in orig_list]
dist_list = np.array(dist_list)
orig_len = np.array(orig_len)
mask = dist_list!=100000
reduced_dist_list = dist_list[mask]
reduced_orig_len = orig_len[mask]
ratio_list =  [reduced_dist_list[i]/reduced_orig_len[i] for i in range(len(reduced_dist_list))]
ratio = np.mean(ratio_list)

print(ratio)
print("ga success rate {:0.2f}".format(np.mean(success_rate)))
print('Median number of modifications ' , np.median([x for x in dist_list if x != 100000]))
print("ratio",ratio)
print("average time ",np.mean(times))

0.10876844461305224
ga success rate 1.00
Median number of modifications  6.0
ratio 0.10876844461305224
average time  362.56428091049196


In [31]:
orig_list, orig_label_list, adv_list, dist_list,times = pickle.load(open("base_results1.pkl","rb"))
success_rate = [0 if dist_list[i] ==100000 else 1 for i in range(len(dist_list))]
orig_len = [np.sum(np.sign(x)) for x in orig_list]
dist_list = np.array(dist_list)
orig_len = np.array(orig_len)
mask = dist_list!=100000
reduced_dist_list = dist_list[mask]
reduced_orig_len = orig_len[mask]
# print(dist_list)
ratio_list =  [1/reduced_orig_len[i] for i in range(len(reduced_dist_list))]
ratio = np.mean(ratio_list)

print("1 attack success rate {:0.2f}".format(np.mean(success_rate)))
print('Median number of modifications ' , 1)
print("ratio",ratio)
print("average time ",np.mean(times))

1 attack success rate 0.22
Median number of modifications  1
ratio 0.015600765936504663
average time  2.8481680870056154


In [32]:
orig_list, orig_label_list, adv_list, dist_list,times = pickle.load(open("greedy_results1.pkl","rb"))
success_rate = [0 if dist_list[i] ==100000 else 1 for i in range(len(dist_list))]
orig_len = [np.sum(np.sign(x)) for x in orig_list]
dist_list = np.array(dist_list)
orig_len = np.array(orig_len)
mask = dist_list!=100000
reduced_dist_list = dist_list[mask]
reduced_orig_len = orig_len[mask]
ratio_list =  [reduced_dist_list[i]/reduced_orig_len[i] for i in range(len(reduced_dist_list))]
ratio = np.mean(ratio_list)

print("greedy attack success rate {:0.2f}".format(np.mean(success_rate)))
print('Median number of modifications ' , np.median([x for x in dist_list if x != 100000]))
print("ratio",ratio)
print("average time ",np.mean(times))

greedy attack success rate 1.00
Median number of modifications  16.0
ratio 0.2736858458573859
average time  37.72437335014343


In [33]:
orig_list, orig_label_list, adv_list, dist_list,times = pickle.load(open("gai_results.pkl","rb"))
success_rate = [0 if dist_list[i] ==100000 else 1 for i in range(len(dist_list))]
orig_len = [np.sum(np.sign(x)) for x in orig_list]
dist_list = np.array(dist_list)
orig_len = np.array(orig_len)
mask = dist_list!=100000
reduced_dist_list = dist_list[mask]
reduced_orig_len = orig_len[mask]
ratio_list =  [reduced_dist_list[i]/reduced_orig_len[i] for i in range(len(reduced_dist_list))]
ratio = np.mean(ratio_list)

print("gai attack success rate {:0.2f}".format(np.mean(success_rate)))
print('Median number of modifications ' , np.median([x for x in dist_list if x != 100000]))
print("ratio",ratio)
print("average time ",np.mean(times))

gai attack success rate 0.82
Median number of modifications  6.0
ratio 0.10593560114132958
average time  15.18982174396515


In [35]:
orig_list, orig_label_list, adv_list, dist_list,times = pickle.load(open("ps_results.pkl","rb"))
success_rate = [0 if dist_list[i] ==100000 else 1 for i in range(len(dist_list))]
orig_len = [np.sum(np.sign(x)) for x in orig_list]
dist_list = np.array(dist_list)
orig_len = np.array(orig_len)
mask = dist_list!=100000
reduced_dist_list = dist_list[mask]
reduced_orig_len = orig_len[mask]
ratio_list =  [reduced_dist_list[i]/reduced_orig_len[i] for i in range(len(reduced_dist_list))]
ratio = np.mean(ratio_list)

print("ps attack success rate {:0.2f}".format(np.mean(success_rate)))
print('Median number of modifications ' , np.median([x for x in dist_list if x != 100000]))
print("ratio",ratio)
print("average time ",np.mean(times))

ps attack success rate 0.94
Median number of modifications  4.0
ratio 0.06834997424493047
average time  378.4963409566879


In [25]:
visual_idx = 24
display_utils.visualize_attack(sess, model, dataset, orig_list[visual_idx], adv_list[visual_idx])

Original Prediction = Positive. (Confidence = 99.95) 


---------  After attack -------------
New Prediction = Negative. (Confidence = 92.77) 


In [ ]:
print('Average number of changed wrods = ', np.mean(dist_list))

In [ ]:
## Save success
with open('attack_results_final.pkl', 'wb') as f:
    pickle.dump((test_list, orig_list, orig_label_list, adv_list, dist_list), f)
    


In [ ]:
import display_utils

In [ ]:
visual_idx = 24

display_utils.visualize_attack2(dataset, test_list[visual_idx], orig_list[visual_idx], adv_list[visual_idx], orig_label_list[visual_idx])

In [ ]:
src_text[0]

In [ ]:
orig_text[0]

In [ ]:
adv_text[0]

In [ ]:
## Baseline
koontz's

# Extensive Test

In [36]:
TEST_SIZE = 1000
all_test_idx = []
for i in range(10):
    test_idx = np.random.choice(len(dataset.test_y), TEST_SIZE, replace=False)
    all_test_idx.append(test_idx)

In [37]:
ga_atttack = GeneticAtack(sess, model, batch_model, neighbour_model, dataset, dist_mat, 
                                  skip_list,
                                  goog_lm, max_iters=30, 
                                   pop_size=pop_size,
                                  
                                  n1 = n1,
                                  n2 = 4,
                                 use_lm =      True, use_suffix=False)
ps_atttack = ParticleSwampAttack(sess, model, batch_model, neighbour_model, dataset, dist_mat, 
                                  skip_list,
                                  goog_lm, max_iters=30, 
                                   pop_size=pop_size,
                                  n1 = n1,
                                  n2 = 4,
                                 use_lm =      True, use_suffix=False)

In [42]:
def run_algo(attacker,test_idx,folder,idx):
    test_len = []
    for i in range(TEST_SIZE):
        test_len.append(len(dataset.test_seqs2[test_idx[i]]))
    print('Shortest sentence in our test set is %d words' %np.min(test_len))

    test_list = []
    orig_list = []
    orig_label_list = []
    adv_list = []
    dist_list = []

    times = []
    for i in range(TEST_SIZE):
    # for x in [ 9554, 20939,  5709,  5105,  7783,  1064,  8223, 19317, 19096]:
    #     k = x
        k = test_idx[i]
        x_orig = test_x[k]
        orig_label = test_y[k]
        orig_preds=  model.predict(sess, x_orig[np.newaxis, :])[0]
        if np.argmax(orig_preds) != orig_label:

            continue
        x_len = np.sum(np.sign(x_orig))
        if x_len >= 100:
            continue
        print(k)
        print('****** ', len(test_list) + 1, ' ********')
        test_list.append(k)
        orig_list.append(x_orig)
        target_label = 1 if orig_label == 0 else 0
        orig_label_list.append(orig_label)
        start = time.time()
    #     x_adv = gai_atttack.attack( x_orig, target_label)
        x_adv = attacker.attack( x_orig, target_label)
        end = time.time()

        times.append(end-start)
        adv_list.append(x_adv)
        if x_adv is None:
            print('%d failed' %(k))
            dist_list.append(100000)
        else:
            num_changes = np.sum(x_orig != x_adv)
            print('%d - %d changed.' %(k, num_changes))
            dist_list.append(num_changes)
            # display_utils.visualize_attack(sess, model, dataset, x_orig, x_adv)
        print('--------------------------')
        if (len(test_list)>= 50):
            break
    file_path = folder+"ps_results"+str(idx)+".pkl"
    if not os.path.isdir(folder):
        os.mkdir(folder)
    with open(file_path, 'wb') as f:
        pickle.dump((orig_list, orig_label_list, adv_list, dist_list,times), f)

In [ ]:
for i in range(10):
    run_algo(ga_atttack,all_test_idx[i],"ga_results/",i)

Shortest sentence in our test set is 35 words
7365
******  1  ********
		 0  --  0.029023236
start
finish
		 1  --  0.118564874
start
finish
		 2  --  0.4020019
start
finish
		 3  --  0.53913426
7365 - 5 changed.
--------------------------
10584
******  2  ********
		 0  --  0.0019698509
start
finish
		 1  --  0.00251124
start
finish
		 2  --  0.0046438044
start
finish
		 3  --  0.02227236
start
finish
		 4  --  0.028117405
start
finish
		 5  --  0.038880195
start
finish
		 6  --  0.059513003
start
finish
		 7  --  0.08588862
start
finish
		 8  --  0.08588862
start
finish
		 9  --  0.10919512
start
finish
		 10  --  0.2188349
start
finish
		 11  --  0.2188349
start
finish
		 12  --  0.36939695
start
finish
		 13  --  0.44178602
start
finish
		 14  --  0.53677887
10584 - 15 changed.
--------------------------
21164
******  3  ********
		 0  --  0.15783246
start
finish
		 1  --  0.35790318
start
finish
		 2  --  0.69432676
21164 - 4 changed.
--------------------------
7527
******  4  ***

		 0  --  0.37443838
start
finish
		 1  --  0.5002625
4392 - 3 changed.
--------------------------
19930
******  34  ********
		 0  --  0.10240175
start
finish
		 1  --  0.23533933
start
finish
		 2  --  0.28689
start
finish
		 3  --  0.61085624
19930 - 6 changed.
--------------------------
18304
******  35  ********
		 0  --  0.00085613393
start
finish
		 1  --  0.0030392783
start
finish
		 2  --  0.0030392783
start
finish
		 3  --  0.0037691274
start
finish
		 4  --  0.004891747
start
finish
		 5  --  0.017722556
start
finish
		 6  --  0.17499973
start
finish
		 7  --  0.18129241
start
finish
		 8  --  0.19676398
start
finish
		 9  --  0.35347408
start
finish
		 10  --  0.45036247
start
finish
		 11  --  0.49634996
start
finish
		 12  --  0.7144535
18304 - 13 changed.
--------------------------
5969
******  36  ********
		 0  --  0.26917547
start
finish
		 1  --  0.35393232
start
finish
		 2  --  0.64936745
5969 - 4 changed.
--------------------------
24228
******  37  ********
		 0 

finish
		 21  --  0.4495854
start
finish
		 22  --  0.4495854
start
finish
		 23  --  0.4495854
start
finish
		 24  --  0.4495854
start
finish
		 25  --  0.4495854
start
finish
		 26  --  0.4495854
start
finish
		 27  --  0.4495854
start
finish
		 28  --  0.4495854
start
finish
		 29  --  0.4495854
start
finish
9940 failed
--------------------------
6298
******  10  ********
		 0  --  0.25524294
start
finish
		 1  --  0.4269091
start
finish
		 2  --  0.47543758
start
finish
		 3  --  0.8178524
6298 - 6 changed.
--------------------------
12196
******  11  ********
		 0  --  0.4886755
start
finish
		 1  --  0.6641229
12196 - 2 changed.
--------------------------
1088
******  12  ********
		 0  --  0.007651821
start
finish
		 1  --  0.015516085
start
finish
		 2  --  0.02966521
start
finish
		 3  --  0.062656194
start
finish
		 4  --  0.062656194
start
finish
		 5  --  0.12027101
start
finish
		 6  --  0.12027101
start
finish
		 7  --  0.29109934
start
finish
		 8  --  0.29109934
start
f

finish
		 2  --  0.0197022
start
finish
		 3  --  0.0197022
start
finish
		 4  --  0.086760096
start
finish
		 5  --  0.16027449
start
finish
		 6  --  0.53455174
24205 - 11 changed.
--------------------------
8307
******  37  ********
		 0  --  0.15566257
start
finish
		 1  --  0.15566257
start
finish
		 2  --  0.21938112
start
finish
		 3  --  0.39107266
start
finish
		 4  --  0.44494095
start
finish
		 5  --  0.4731422
start
finish
		 6  --  0.4731422
start
finish
		 7  --  0.58747166
8307 - 9 changed.
--------------------------
2675
******  38  ********
		 0  --  0.010048459
start
finish
		 1  --  0.017316535
start
finish
		 2  --  0.019541787
start
finish
		 3  --  0.094598584
start
finish
		 4  --  0.14150497
start
finish
		 5  --  0.37105542
start
finish
		 6  --  0.37105542
start
finish
		 7  --  0.37105542
start
finish
		 8  --  0.45137826
start
finish
		 9  --  0.7748957
2675 - 13 changed.
--------------------------
9511
******  39  ********
		 0  --  0.0055784653
start
finis

finish
		 3  --  0.037842546
start
finish
		 4  --  0.06667251
start
finish
		 5  --  0.08708266
start
finish
		 6  --  0.12417323
start
finish
		 7  --  0.17713161
start
finish
		 8  --  0.5107227
21923 - 12 changed.
--------------------------
11647
******  16  ********
		 0  --  0.00083395385
start
finish
		 1  --  0.0036360417
start
finish
		 2  --  0.011955233
start
finish
		 3  --  0.011955233
start
finish
		 4  --  0.018791137
start
finish
		 5  --  0.036646973
start
finish
		 6  --  0.4620341
start
finish
		 7  --  0.6920247
11647 - 9 changed.
--------------------------
9865
******  17  ********
		 0  --  0.0013464515
start
finish
		 1  --  0.0013464515
start
finish
		 2  --  0.0029799105
start
finish
		 3  --  0.003951098
start
finish
		 4  --  0.027625345
start
finish
		 5  --  0.25862327
start
finish
		 6  --  0.50354904
9865 - 6 changed.
--------------------------
22348
******  18  ********
		 0  --  0.51077074
22348 - 1 changed.
--------------------------
4018
******  19  *

...

finish
		 4  --  0.26329306
start
finish
		 5  --  0.2903002
start
finish
		 6  --  0.39780536
start
finish
		 7  --  0.39780536
start
finish
		 8  --  0.45590687
start
finish
		 9  --  0.45590687
start
finish
		 10  --  0.45590687
start
finish
		 11  --  0.53714854
18985 - 14 changed.
--------------------------
18969
******  30  ********
		 0  --  0.59939677
18969 - 1 changed.
--------------------------
10682
******  31  ********
		 0  --  0.02917794
start
finish
		 1  --  0.031775612
start
finish
		 2  --  0.09584348
start
finish
		 3  --  0.117679626
start
finish
		 4  --  0.15176159
start
finish
		 5  --  0.21598756
start
finish
		 6  --  0.21598756
start
finish
		 7  --  0.521229
10682 - 7 changed.
--------------------------
23228
******  32  ********
		 0  --  0.97644216
23228 - 1 changed.
--------------------------
12209
******  33  ********
		 0  --  0.13807477
start
finish
		 1  --  0.36451778
start
finish
		 2  --  0.3868082
start
finish
		 3  --  0.791125
12209 - 5 changed.


finish
		 19  --  0.43548998
start
finish
		 20  --  0.5666142
24461 - 22 changed.
--------------------------
3089
******  11  ********
		 0  --  0.24527943
start
finish
		 1  --  0.3063325
start
finish
		 2  --  0.39768848
start
finish
		 3  --  0.44909623
start
finish
		 4  --  0.4682851
start
finish
		 5  --  0.51015985
3089 - 6 changed.
--------------------------
19793
******  12  ********
		 0  --  0.5963742
19793 - 1 changed.
--------------------------
17163
******  13  ********
		 0  --  0.28327018
start
finish
		 1  --  0.30921525
start
finish
		 2  --  0.32554212
start
finish
		 3  --  0.36936575
start
finish
		 4  --  0.6205507
17163 - 4 changed.
--------------------------
474
******  14  ********
		 0  --  0.0639085
start
finish
		 1  --  0.28127894
start
finish
		 2  --  0.5082577
474 - 5 changed.
--------------------------
328
******  15  ********
		 0  --  0.0073529575
start
finish
		 1  --  0.021068117
start
finish
		 2  --  0.43981338
start
finish
		 3  --  0.48471007
s

4668
******  41  ********
		 0  --  6.255001e-07
start
finish
		 1  --  1.2572551e-06
start
finish
		 2  --  3.3694214e-06
start
finish
		 3  --  5.6377307e-06
start
finish
		 4  --  3.0916384e-05
start
finish
		 5  --  3.0916384e-05
start
finish
		 6  --  3.0916384e-05
start
finish
		 7  --  6.1821265e-05
start
finish
		 8  --  6.1821265e-05
start
finish
		 9  --  0.00016865725
start
finish
		 10  --  0.00016865725
start
finish
		 11  --  0.00017495791
start
finish
		 12  --  0.00057730655
start
finish
		 13  --  0.00057730655
start
finish
		 14  --  0.0006068615
start
finish
		 15  --  0.0006068615
start
finish
		 16  --  0.0022317455
start
finish
		 17  --  0.009497446
start
finish
		 18  --  0.009497446
start
finish
		 19  --  0.011911906
start
finish
		 20  --  0.020083036
start
finish
		 21  --  0.06239263
start
finish
		 22  --  0.2608643
start
finish
		 23  --  0.5307559
4668 - 23 changed.
--------------------------
14425
******  42  ********
		 0  --  0.8394877
14425 - 1 chang

finish
		 2  --  0.22617273
start
finish
		 3  --  0.3650578
start
finish
		 4  --  0.3738314
start
finish
		 5  --  0.53183043
23766 - 4 changed.
--------------------------
16993
******  21  ********
		 0  --  0.15634967
start
finish
		 1  --  0.4301386
start
finish
		 2  --  0.5400893
16993 - 3 changed.
--------------------------
6184
******  22  ********
		 0  --  0.04725755
start
finish
		 1  --  0.28950807
start
finish
		 2  --  0.482742
start
finish
		 3  --  0.9235412
6184 - 5 changed.
--------------------------
24147
******  23  ********
		 0  --  0.030647388
start
finish
		 1  --  0.12252966
start
finish
		 2  --  0.16975014
start
finish
		 3  --  0.42244115
start
finish
		 4  --  0.7194301
24147 - 6 changed.
--------------------------
2780
******  24  ********
		 0  --  0.032191113
start
finish
		 1  --  0.09604118
start
finish
		 2  --  0.6199945
2780 - 5 changed.
--------------------------
22008
******  25  ********
		 0  --  0.033404086
start
finish
		 1  --  0.04276182
st

finish
		 4  --  0.91051644
8062 - 5 changed.
--------------------------
9069
******  8  ********
		 0  --  0.8294702
9069 - 1 changed.
--------------------------
3239
******  9  ********
		 0  --  0.0045786803
start
finish
		 1  --  0.013281965
start
finish
		 2  --  0.04380735
start
finish
		 3  --  0.09022841
start
finish
		 4  --  0.43130454
start
finish
		 5  --  0.43130454
start
finish
		 6  --  0.5139555
3239 - 9 changed.
--------------------------
13716
******  10  ********
		 0  --  0.8389563
13716 - 1 changed.
--------------------------
7025
******  11  ********
		 0  --  0.012008284
start
finish
		 1  --  0.012008284
start
finish
		 2  --  0.04107061
start
finish
		 3  --  0.05401974
start
finish
		 4  --  0.17438546
start
finish
		 5  --  0.94511724
7025 - 7 changed.
--------------------------
20033
******  12  ********
		 0  --  0.00022645379
start
finish
		 1  --  0.0013972372
start
finish
		 2  --  0.002737953
start
finish
		 3  --  0.008817787
start
finish
		 4  --  0.0

In [ ]:
for i in range(10):
    run_algo(ps_atttack,all_test_idx[i],"ps_results/",i)